In [1]:
import warnings
warnings.filterwarnings('ignore')
    

In [2]:
import pandas as pd
import math

In [3]:
df_train=r'D:/EDUCATION/Data Science/Python projects/Consumer_Complaints_train.csv'
df_test=r'D:/EDUCATION/Data Science/Python projects/Consumer_Complaints_test_share.csv'
cd_train=pd.read_csv(df_train)
cd_test=pd.read_csv(df_test)

In [4]:
cd_train.head(10)

Date received                  Product                  Sub-product  \
0    2014-05-15              Credit card                          NaN   
1    2014-09-18  Bank account or service  (CD) Certificate of deposit   
2    2014-03-13         Credit reporting                          NaN   
3    2015-07-17              Credit card                          NaN   
4    2014-11-20              Credit card                          NaN   
5    2014-06-26                 Mortgage               Other mortgage   
6    2012-09-28                 Mortgage               Other mortgage   
7    2015-05-06                 Mortgage                 FHA mortgage   
8    2013-02-25              Credit card                          NaN   
9    2016-03-30  Bank account or service             Checking account   

                                      Issue       Sub-issue  \
0                         Billing statement             NaN   
1  Making/receiving payments, sending money             NaN   
2    Incorrect information on credit report  Account status   
3                         Billing statement             NaN   
4                         Transaction issue             NaN   
5  Loan modification,collection,foreclosure             NaN   
6  Loan servicing, payments, escrow account             NaN   
7  Loan modification,collection,foreclosure             NaN   
8  Credit card protection / Debt protection             NaN   
9                  Deposits and withdrawals             NaN   

                        Consumer complaint narrative  \
0                                                NaN   
1                                                NaN   
2                                                NaN   
3  My credit card statement from US Bank, XXXX. X...   
4                                                NaN   
5                                                NaN   
6                                                NaN   
7  I have a mortgage with Quicken Loans. From XXX...   
8                                                NaN   
9  I put my settlement check in to bank of americ...   

                             Company public response                Company  \
0                                                NaN  Wells Fargo & Company   
1                                                NaN      Santander Bank US   
2                                                NaN                Equifax   
3   Company chooses not to provide a public response           U.S. Bancorp   
4                                                NaN        Bank of America   
5                                                NaN        Bank of America   
6                                                NaN                  Ocwen   
7                                                NaN          Quicken Loans   
8                                                NaN               Discover   
9  Company has responded to the consumer and the ...        Bank of America   

  State ZIP code            Tags Consumer consent provided? Submitted via  \
0    MI    48342  Older American                        NaN           Web   
1    PA    18042             NaN                        NaN      Referral   
2    CA    92427             NaN                        NaN      Referral   
3    GA    305XX  Older American           Consent provided           Web   
4    MA    02127             NaN                        NaN           Web   
5    WI    54313             NaN                        NaN      Referral   
6    FL    33168             NaN                        NaN      Referral   
7    GA    300XX             NaN           Consent provided           Web   
8    OH    45640             NaN                        NaN           Web   
9    TX    787XX             NaN           Consent provided           Web   

  Date sent to company     Company response to consumer Timely response?  \
0           2014-05-16          Closed with explanation              Yes   
1           2014-

In [5]:
import numpy as np
cd_train['Consumer disputed?']=np.where(cd_train['Consumer disputed?']=='Yes',0,1)
cd_train['Consumer disputed?']

0         1
1         1
2         1
3         1
4         1
         ..
478416    1
478417    1
478418    1
478419    1
478420    1
Name: Consumer disputed?, Length: 478421, dtype: int32

In [6]:
for col in['Date received','Date sent to company']:
    cd_train[col]=pd.to_datetime(cd_train[col],infer_datetime_format=True)
    cd_test[col]=pd.to_datetime(cd_test[col],infer_datetime_format=True)

In [7]:
cd_train[col]

0        2014-05-16
1        2014-09-24
2        2014-04-03
3        2015-07-17
4        2014-11-28
            ...    
478416   2015-07-01
478417   2013-06-21
478418   2014-09-09
478419   2012-09-24
478420   2014-10-30
Name: Date sent to company, Length: 478421, dtype: datetime64[ns]

In [8]:
cd_test[col]

0        2014-01-17
1        2016-03-31
2        2012-03-09
3        2016-01-12
4        2013-08-23
            ...    
119601   2012-09-21
119602   2016-07-21
119603   2015-06-12
119604   2014-02-27
119605   2015-02-11
Name: Date sent to company, Length: 119606, dtype: datetime64[ns]

In [9]:
cd_train['day_diff']=pd.to_numeric((cd_train['Date sent to company']-cd_train['Date received'])/np.timedelta64(1, 'M'))
cd_test['day_diff']=pd.to_numeric((cd_test['Date sent to company']-cd_test['Date received'])/np.timedelta64(1,'M'))

In [10]:
for col in ['Date received','Date sent to company']:
    cd_train.drop([col],1,inplace=True)
    cd_test.drop([col],1,inplace=True)

In [11]:
for col in cd_train.select_dtypes(['object']).columns:
    print(col,':',cd_train[col].nunique())

Product : 12
Sub-product : 47
Issue : 95
Sub-issue : 68
Consumer complaint narrative : 74019
Company public response : 10
Company : 3276
State : 62
ZIP code : 25962
Tags : 3
Consumer consent provided? : 4
Submitted via : 6
Company response to consumer : 7
Timely response? : 2


In [12]:
for col in cd_train.select_dtypes(['object']).columns:
    print(col,':',cd_train[col].unique())

Product : ['Credit card' 'Bank account or service' 'Credit reporting' 'Mortgage'
 'Debt collection' 'Student loan' 'Consumer Loan' 'Money transfers'
 'Prepaid card' 'Payday loan' 'Other financial service' 'Virtual currency']
Sub-product : [nan '(CD) Certificate of deposit' 'Other mortgage' 'FHA mortgage'
 'Checking account' 'Conventional fixed mortgage' 'Medical'
 'Conventional adjustable mortgage (ARM)' 'Non-federal student loan'
 'Home equity loan or line of credit' 'Vehicle lease' 'Mortgage'
 'I do not know' 'Vehicle loan' 'Credit card'
 'International money transfer' 'Other (i.e. phone, health club, etc.)'
 'Other bank product/service' 'Auto' 'Payday loan'
 'Government benefit payment card' 'Installment loan' 'Reverse mortgage'
 'Savings account' 'Other special purpose card'
 'Federal student loan servicing' 'Domestic (US) money transfer'
 'VA mortgage' 'Personal line of credit'
 'Cashing a check without an account' 'Second mortgage' 'Mobile wallet'
 'Payroll card' 'General purpose

Company public response : [nan 'Company chooses not to provide a public response'
 'Company has responded to the consumer and the CFPB and chooses not to provide a public response'
 'Company believes it acted appropriately as authorized by contract or law'
 'Company believes complaint caused principally by actions of third party outside the control or direction of the company'
 'Company believes the complaint is the result of a misunderstanding'
 'Company disputes the facts presented in the complaint'
 "Company can't verify or dispute the facts in the complaint"
 'Company believes complaint is the result of an isolated error'
 'Company believes complaint represents an opportunity for improvement to better serve consumers'
 'Company believes complaint relates to a discontinued policy or procedure']
Company : ['Wells Fargo & Company' 'Santander Bank US' 'Equifax' ...
 'CLAYTON AUTOS, INC' 'ALCHRO INC.' 'Advance Title & Abstract, Inc.']
State : ['MI' 'PA' 'CA' 'GA' 'MA' 'WI' 'FL' 'OH' 'TX

In [13]:
cd_train['Tags'].value_counts()

Older American                   39064
Servicemember                    22592
Older American, Servicemember     5550
Name: Tags, dtype: int64

In [14]:
for col in cd_train['Tags']:
    print(col)

Older American
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American, Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
Servicemember
nan
Older American
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
Servicemember
nan
nan
nan
nan
nan
Older American
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
Servicemember
Older American
Older American
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
Older American, 

nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
Older American
nan
nan
nan
nan
nan
Older American
nan
nan
nan
Older American
nan
nan
nan
nan
Servicemember
Older American, Servicemember
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American, Servicemember
nan
nan
Older American
nan
nan
nan
nan
Older American
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
Older American, Servicemember
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American, Servicemember
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
Older American
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
Older American
nan
Older American
nan
nan
nan
nan
Older American
nan
na

nan
nan
Older American, Servicemember
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
Older American, Servicemember
nan
Older American
nan
nan
nan
nan
nan
nan
nan
Older American, Servicemember
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
Older American
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
Older American
nan
nan
Older American
Older American
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
Older American
nan
nan
nan
nan
Older American, Servicemember
Servicemember
nan
nan
na

nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American, Servicemember
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
Older American
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
Older American
nan
nan
Older American
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
Older American
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American, Servicemember

nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
Older American, Servicemember
nan
Older American
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
Older American, Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
Older American
Servicemember
nan
nan
nan
Older American
nan
nan
Servicemember
nan
Older American
nan
nan
nan
Servicemember
nan
nan
nan
nan
Servicemember
nan
Older American
Servicemember
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
Older American
nan
nan
Older American
nan
nan
Servicemember
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
Older American
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older A

...

nan
nan
Servicemember
nan
Older American
nan
nan
nan
nan
Older American
nan
nan
Older American
Servicemember
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
Older American
nan
Older American
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
Older American
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
Older American, Servicemember
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
Servicemember
nan
nan
nan
Older American
nan
Servicemember
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
Older American, Servicemember
nan
nan
nan
Older American
Older American
nan
nan
Older American
Older Americ

nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
Older American
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
Servicemember
nan
nan
Older American
nan
Older American
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
Older American
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan

nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American, Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
Older American
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
Older American
Older American
nan
nan
Older American, Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
Older American
Older American, Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American, Servicemember
nan
nan
nan
Older American
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
Older American
nan
nan

nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
Servicemember
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
Older American
nan
nan
Older American
Older American
nan
nan
nan
nan
nan
Older American, Servicemember
nan
nan
Older American
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
Older American
Older American
nan
nan
nan
nan
nan
Older American
nan
Servicemember
Older American
nan
Older American
nan
nan
nan
Older American
Older American
Older American
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older

nan
nan
nan
nan
nan
Servicemember
Older American
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
Older American, Servicemember
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
Servicemember
nan
Older American, Servicemember
nan
nan
nan
nan
Servicemember
nan
nan
nan
Older American
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American, Servicemember
Servicemember
Servicemember
nan
nan
Servicemember
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
Servicemember
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan


In [15]:
cd_train.isnull().sum()

Product                              0
Sub-product                     138473
Issue                                0
Sub-issue                       292625
Consumer complaint narrative    403327
Company public response         388029
Company                              0
State                             3839
ZIP code                          3848
Tags                            411215
Consumer consent provided?      342934
Submitted via                        0
Company response to consumer         0
Timely response?                     0
Consumer disputed?                   0
Complaint ID                         0
day_diff                             0
dtype: int64

In [16]:
for col in ['Tags','Company public response']:
    varname=col.replace('-','_').replace('?','').replace("",'_')+'_isNan'
    cd_train[varname]=np.where(pd.isnull(cd_train[col]),1,0)
    cd_train.drop([col],1,inplace=True)
    cd_test[varname]=np.where(pd.isnull(cd_test[col]),1,0)
    cd_test.drop([col],1,inplace=True)

In [17]:
cd_train.dtypes

Product                                                   object
Sub-product                                               object
Issue                                                     object
Sub-issue                                                 object
Consumer complaint narrative                              object
Company                                                   object
State                                                     object
ZIP code                                                  object
Consumer consent provided?                                object
Submitted via                                             object
Company response to consumer                              object
Timely response?                                          object
Consumer disputed?                                         int32
Complaint ID                                               int64
day_diff                                                 float64
_T_a_g_s__isNan          

In [18]:
for col in cd_train.select_dtypes(['object']).columns:
    print(col,':',cd_train[col].nunique())

Product : 12
Sub-product : 47
Issue : 95
Sub-issue : 68
Consumer complaint narrative : 74019
Company : 3276
State : 62
ZIP code : 25962
Consumer consent provided? : 4
Submitted via : 6
Company response to consumer : 7
Timely response? : 2


In [19]:
k=cd_train['State'].value_counts()
for val in k.axes[0][0:15]:
    varname='State_'+val.replace(',','_').replace(' ','_')
    cd_train[varname]=np.where(cd_train['State']==val,1,0)
    cd_test[varname]=np.where(cd_test['State']==val,1,0)
del cd_train['State']
del cd_test['State']

In [20]:
for col in cd_train.select_dtypes(['object']).columns:
    print(col,':',cd_train[col].nunique())
    

Product : 12
Sub-product : 47
Issue : 95
Sub-issue : 68
Consumer complaint narrative : 74019
Company : 3276
ZIP code : 25962
Consumer consent provided? : 4
Submitted via : 6
Company response to consumer : 7
Timely response? : 2


In [21]:
for col in ['Product','Submitted via','Company response to consumer','Timely response?']:
    temp=pd.get_dummies(cd_train[col],prefix=col,drop_first=True)
    cd_train=pd.concat([temp,cd_train],1)
    cd_train.drop([col],1,inplace=True)
    
    temp=pd.get_dummies(cd_test[col],prefix=col,drop_first=True)
    cd_test=pd.concat([temp,cd_test],1)
    cd_test.drop([col],1,inplace=True)

    
    

In [22]:
for col in cd_train.select_dtypes(['object']).columns:
    print(col,':',cd_train[col].nunique())

Sub-product : 47
Issue : 95
Sub-issue : 68
Consumer complaint narrative : 74019
Company : 3276
ZIP code : 25962
Consumer consent provided? : 4


In [23]:
cd_train.shape

(478421, 50)

In [24]:
cd_test.shape

(119606, 49)

In [25]:
for col in ['ZIP code','Company']:
    cd_train.drop([col],1,inplace=True)
    cd_test.drop([col],1,inplace=True)

In [26]:
for col in cd_train.select_dtypes(['object']).columns:
    print(col,':',cd_train[col].nunique())

Sub-product : 47
Issue : 95
Sub-issue : 68
Consumer complaint narrative : 74019
Consumer consent provided? : 4


In [27]:
cd_train.dtypes

Timely response?_Yes                                              uint8
Company response to consumer_Closed with explanation              uint8
Company response to consumer_Closed with monetary relief          uint8
Company response to consumer_Closed with non-monetary relief      uint8
Company response to consumer_Closed with relief                   uint8
Company response to consumer_Closed without relief                uint8
Company response to consumer_Untimely response                    uint8
Submitted via_Fax                                                 uint8
Submitted via_Phone                                               uint8
Submitted via_Postal mail                                         uint8
Submitted via_Referral                                            uint8
Submitted via_Web                                                 uint8
Product_Consumer Loan                                             uint8
Product_Credit card                                             

In [28]:
cd_train['Super']=cd_train['Sub-product']+cd_train['Issue']+cd_train['Sub-issue']+cd_train['Consumer complaint narrative']+cd_train['Consumer consent provided?']
del cd_train['Issue']
del cd_train['Sub-issue']
del cd_train['Consumer complaint narrative']
del cd_train['Consumer consent provided?']
cd_train["Super"]=np.where(pd.isnull(cd_train["Super"]),'NaN',cd_train["Super"])
cd_train["Super"].astype(str)

0         NaN
1         NaN
2         NaN
3         NaN
4         NaN
         ... 
478416    NaN
478417    NaN
478418    NaN
478419    NaN
478420    NaN
Name: Super, Length: 478421, dtype: object

In [29]:
cd_test['Super']=cd_test['Consumer consent provided?']+cd_test['Sub-product']+cd_test['Issue']+','+cd_test['Sub-issue']+','+cd_test['Consumer complaint narrative']
del cd_test['Issue']
del cd_test['Sub-issue']
del cd_test['Consumer consent provided?']
del cd_test['Consumer complaint narrative']
cd_test["Super"]=np.where(pd.isnull(cd_test["Super"]),'NaN',cd_test['Super'])
cd_test['Super'].astype(str)
    

0         NaN
1         NaN
2         NaN
3         NaN
4         NaN
         ... 
119601    NaN
119602    NaN
119603    NaN
119604    NaN
119605    NaN
Name: Super, Length: 119606, dtype: object

In [30]:
cd_test.isnull().sum()

Timely response?_Yes                                                0
Company response to consumer_Closed with explanation                0
Company response to consumer_Closed with monetary relief            0
Company response to consumer_Closed with non-monetary relief        0
Company response to consumer_Closed with relief                     0
Company response to consumer_Closed without relief                  0
Company response to consumer_Untimely response                      0
Submitted via_Fax                                                   0
Submitted via_Phone                                                 0
Submitted via_Postal mail                                           0
Submitted via_Referral                                              0
Submitted via_Web                                                   0
Product_Consumer Loan                                               0
Product_Credit card                                                 0
Product_Credit repor

In [32]:
cd_train.isnull().sum()

Timely response?_Yes                                                 0
Company response to consumer_Closed with explanation                 0
Company response to consumer_Closed with monetary relief             0
Company response to consumer_Closed with non-monetary relief         0
Company response to consumer_Closed with relief                      0
Company response to consumer_Closed without relief                   0
Company response to consumer_Untimely response                       0
Submitted via_Fax                                                    0
Submitted via_Phone                                                  0
Submitted via_Postal mail                                            0
Submitted via_Referral                                               0
Submitted via_Web                                                    0
Product_Consumer Loan                                                0
Product_Credit card                                                  0
Produc

In [34]:
cd_train.head(4)

Timely response?_Yes  Company response to consumer_Closed with explanation  \
0                     1                                                  1      
1                     1                                                  0      
2                     1                                                  0      
3                     1                                                  0      

   Company response to consumer_Closed with monetary relief  \
0                                                  0          
1                                                  0          
2                                                  0          
3                                                  1          

   Company response to consumer_Closed with non-monetary relief  \
0                                                  0              
1                                                  0              
2                                                  1              
3                                                  0              

   Company response to consumer_Closed with relief  \
0                                                0   
1                                                0   
2                                                0   
3                                                0   

   Company response to consumer_Closed without relief  \
0                                                  0    
1                                                  0    
2                                                  0    
3                                                  0    

   Company response to consumer_Untimely response  Submitted via_Fax  \
0                                               0                  0   
1                                               0                  0   
2                                               0                  0   
3                                               0                  0   

   Submitted via_Phone  Submitted via_Postal mail  ...  State_PA  State_IL  \
0                    0                          0  ...         0         0   
1                    0                          0  ...         1         0   
2                    0                          0  ...         0         0   
3                    0                          0  ...         0         0   

   State_VA  State_MD  State_OH  State_NC  State_MI  State_AZ  State_WA  Super  
0         0         0         0         0         1         0         0    NaN  
1         0         0         0         0         0         0         0    NaN  
2         0         0         0         0         0         0         0    NaN  
3         0         0         0         0         0         0         0    NaN  

[4 rows x 45 columns]

In [35]:
cd_train['Super']

0         NaN
1         NaN
2         NaN
3         NaN
4         NaN
         ... 
478416    NaN
478417    NaN
478418    NaN
478419    NaN
478420    NaN
Name: Super, Length: 478421, dtype: object

In [37]:
from sklearn.model_selection import train_test_split
cd1_train,cd1_test=train_test_split(cd_train,test_size=0.2,random_state=2)

In [39]:
from sklearn.naive_bayes import MultinomialNB

In [45]:
from sklearn.feature_extraction.text import TfidfVectorizer
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem.wordnet import WordNetLemmatizer
lemma=WordNetLemmatizer()
stop=set(stopwords.words('english'))

In [51]:
def split_into_lemmas(message):
    words=word_tokenize(message)
    words_sans_stop=[]
    for word in words:
        if word in stop:continue
        words_sans_stop.append(word)
    return[lemma.lemmatize(word) for word in words_sans_stop]

In [52]:
tfidf=TfidfVectorizer(analyzer=split_into_lemmas,min_df=10,max_df=3000)

In [53]:
tfidf.fit(cd_train['Super'])

TfidfVectorizer(analyzer=<function split_into_lemmas at 0x00000247D4AA13A8>,
                binary=False, decode_error='strict',
                dtype=<class 'numpy.float64'>, encoding='utf-8',
                input='content', lowercase=True, max_df=3000, max_features=None,
                min_df=10, ngram_range=(1, 1), norm='l2', preprocessor=None,
                smooth_idf=True, stop_words=None, strip_accents=None,
                sublinear_tf=False, token_pattern='(?u)\\b\\w\\w+\\b',
                tokenizer=None, use_idf=True, vocabulary=None)

In [55]:
train_data=tfidf.transform(cd_train['Super'])

In [56]:
train_data

<478421x7209 sparse matrix of type '<class 'numpy.float64'>'
	with 1015072 stored elements in Compressed Sparse Row format>

In [ ]:
test_data=tfidf.transformsform(cd_test['Super'])

In [57]:
clf=MultinomialNB()

In [59]:
clf.fit(train_data,cd_train['Consumer disputed?'])

MultinomialNB(alpha=1.0, class_prior=None, fit_prior=True)

In [61]:
final_data=tfidf.transform(cd_train['Super'])

In [62]:
p=clf.predict_proba(final_data)

In [63]:
p.shape

(478421, 2)

In [64]:
p[:0]

array([], shape=(0, 2), dtype=float64)

In [65]:
clf.classes_

array([0, 1])

In [67]:
cd_train['tfidf']=np.where(p[:,0]>=0.5,0,1)

In [68]:
del cd_train['Super']

In [69]:
del cd_train['Sub-product']

In [70]:
test_final_data=tfidf.transform(cd_test['Super'])

In [71]:
test_final_data

<119606x7209 sparse matrix of type '<class 'numpy.float64'>'
	with 249484 stored elements in Compressed Sparse Row format>

In [72]:
r=clf.predict_proba(test_final_data)

In [73]:
r

array([[0.21201201, 0.78798799],
       [0.21201201, 0.78798799],
       [0.21201201, 0.78798799],
       ...,
       [0.21201201, 0.78798799],
       [0.21201201, 0.78798799],
       [0.21201201, 0.78798799]])

In [74]:
cd_test['tfidf']=np.where(r[:,0]>0.5,1,0)

In [76]:
del cd_test['Super']
del cd_test['Sub-product']

KeyError: 'Super'

In [77]:
cd_train.dtypes

Timely response?_Yes                                              uint8
Company response to consumer_Closed with explanation              uint8
Company response to consumer_Closed with monetary relief          uint8
Company response to consumer_Closed with non-monetary relief      uint8
Company response to consumer_Closed with relief                   uint8
Company response to consumer_Closed without relief                uint8
Company response to consumer_Untimely response                    uint8
Submitted via_Fax                                                 uint8
Submitted via_Phone                                               uint8
Submitted via_Postal mail                                         uint8
Submitted via_Referral                                            uint8
Submitted via_Web                                                 uint8
Product_Consumer Loan                                             uint8
Product_Credit card                                             

In [78]:
cd1_train,cd1_test=train_test_split(cd_train,test_size=0.2,random_state=2)

In [79]:
x=cd1_train.drop(['Consumer disputed?','Complaint ID'],1)
y=cd1_train['Consumer disputed?']
k=cd1_test.drop(['Consumer disputed?','Complaint ID'],1)
m=cd1_test['Consumer disputed?']

In [80]:
x.shape

(382736, 42)

In [81]:
y.shape

(382736,)

In [82]:
m.value_counts()

1    75566
0    20119
Name: Consumer disputed?, dtype: int64

In [83]:
y.shape

(382736,)

In [84]:
m.shape

(95685,)

In [85]:
from sklearn.linear_model import LogisticRegression

In [86]:
clf=LogisticRegression()

In [87]:
clf.fit(x,y)

LogisticRegression(C=1.0, class_weight=None, dual=False, fit_intercept=True,
                   intercept_scaling=1, l1_ratio=None, max_iter=100,
                   multi_class='warn', n_jobs=None, penalty='l2',
                   random_state=None, solver='warn', tol=0.0001, verbose=0,
                   warm_start=False)

In [88]:
prediction=clf.predict(k)

In [89]:
from sklearn.metrics import roc_auc_score

In [91]:
prediction

array([1, 1, 1, ..., 1, 1, 1])

In [92]:
m


154142    1
206525    0
26341     1
398527    1
134537    1
         ..
437699    1
325670    1
293448    0
317292    1
73745     0
Name: Consumer disputed?, Length: 95685, dtype: int32

In [99]:
roc_auc_score(prediction,m)

0.7165189079806129

In [102]:
prediction=np.where(clf.predict(cd_test.drop(['Complaint ID'],1))==1,"Yes","No")

In [103]:
prediction

array(['No', 'No', 'No', ..., 'No', 'No', 'No'], dtype='<U3')

In [105]:
submission=pd.DataFrame(list(zip(cd_test['Complaint ID'],list(prediction))),
                        columns=['Complaint ID','Consumer disputed?'])

In [106]:
m.value_counts()

1    75566
0    20119
Name: Consumer disputed?, dtype: int64

In [107]:
submission['Consumer disputed?'].value_counts()

No     97357
Yes    22249
Name: Consumer disputed?, dtype: int64

In [108]:
submission.to_csv('Submission_final.csv',index=False)

In [109]:
cd_train["Consumer disputed?"].value_counts()

1    376990
0    101431
Name: Consumer disputed?, dtype: int64